# Hyperparameter Tuning

In this project we will test different approaches to hyperparameter tuning.

For illustrative purposes, we will use the simplest model we've created in the [Text Classification with Neural Networks](https://github.com/j-n-t/natural_language_processing/blob/master/Text%20Classification%20with%20Neural%20Networks.ipynb) notebook and will try to improve its performance.

In order to do that, we will test the following methods:

* **Grid Search**
* **Random Search**
* **Bayesian Optimization**

### Step 1

We'll start by using **sklearn's GridSearchCV** on our simplest model, the **Dense classifier**. 

#### 1. Perform initial imports

In [1]:
import keras
from keras.datasets import imdb
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Flatten, Dropout
from keras.layers import Embedding

from keras.wrappers.scikit_learn import KerasClassifier

from sklearn.model_selection import GridSearchCV

import os

import numpy as np
import pandas as pd

Using TensorFlow backend.


#### 2. Load data

In [2]:
# create function to load data

def load_data(n_unique_words, n_words_to_skip):
    (x_train, y_train), (x_test, y_test) = imdb.load_data(num_words=n_unique_words, 
                                                          skip_top=n_words_to_skip)
    return (x_train, y_train), (x_test, y_test)

In [3]:
n_unique_words = 10000 #number of most frequent words to consider
n_words_to_skip = 50 #number of most frequent words to ignore

(x_train, y_train), (x_test, y_test) = load_data(n_unique_words, n_words_to_skip)

In [4]:
len(x_train[0])

218

#### 3. Preprocess data

In [5]:
# create function to preprocess data

def preprocess_data(x_train, x_test, max_review_length, pad_type, trunc_type):
    x_train = pad_sequences(x_train, maxlen=max_review_length, 
                            padding=pad_type, truncating=trunc_type, value=0)

    x_test = pad_sequences(x_test, maxlen=max_review_length, 
                           padding=pad_type, truncating=trunc_type, value=0)
    
    return x_train, x_test

In [6]:
max_review_length = 100 #maximum review length of 100 words
pad_type = 'pre' #add padding characters to the start of every review < 100 words
trunc_type = 'pre' #remove words from the beginning of every review > 100 words

x_train, x_test = preprocess_data(x_train, x_test, max_review_length, pad_type, trunc_type)

In [7]:
x_train[0]

array([1415,    2,    2,    2,    2,  215,    2,   77,   52,    2,    2,
        407,    2,   82,    2,    2,    2,  107,  117, 5952,    2,  256,
          2,    2,    2, 3766,    2,  723,    2,   71,    2,  530,  476,
          2,  400,  317,    2,    2,    2,    2, 1029,    2,  104,   88,
          2,  381,    2,  297,   98,    2, 2071,   56,    2,  141,    2,
        194, 7486,    2,    2,  226,    2,    2,  134,  476,    2,  480,
          2,  144,    2, 5535,    2,   51,    2,    2,  224,   92,    2,
        104,    2,  226,   65,    2,    2, 1334,   88,    2,    2,  283,
          2,    2, 4472,  113,  103,    2,    2,    2, 5345,    2,  178,
          2])

In [8]:
len(x_train[0])

100

#### 4. Design and compile model

In [9]:
def create_model(dropout=0.5, n_dense=64):

    model = Sequential(name='model_dense')
    
    model.add(Embedding(10000, 64, input_length=100))
    model.add(Flatten())
    
    model.add(Dense(n_dense, activation='relu'))
    model.add(Dropout(dropout))
    
    model.add(Dense(1, activation='sigmoid'))
    
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    
    return model

#### 5. Create model

In [10]:
model = KerasClassifier(build_fn=create_model, verbose=1)

In our first grid search, we'll try to tune the hyperparameters `epochs` and `batch size`.

#### 6. Define grid search parameters

In [11]:
epochs = [2, 4, 6]
batch_size = [64, 128]

param_grid = {'epochs': epochs, 'batch_size': batch_size}

In [12]:
param_grid

{'epochs': [2, 4, 6], 'batch_size': [64, 128]}

In [13]:
grid_search = GridSearchCV(model, param_grid, cv=3, scoring = 'roc_auc')

#### 7. Perform grid search and print results

In [14]:
%%time

grid_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16666/16666 [==============================] - 7s 395us/step - loss: 0.5391 - accuracy: 0.7074
Epoch 2/2
8334/8334 [==============================] - 0s 49us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16667/16667 [==============================] - 8s 453us/step - loss: 0.5450 - accuracy: 0.6998
Epoch 2/2
8333/8333 [==============================] - 0s 43us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/6
16667/16667 [==============================] - 3s 202us/step - loss: 0.6267 - accuracy: 0.6389
Epoch 2/6
16667/16667 [==============================] - 3s 196us/step - loss: 0.2872 - accuracy: 0.8867
Epoch 3/6
16667/16667 [==============================] - 3s 187us/step - loss: 0.0932 - accuracy: 0.9751
Epoch 4/6
16667/16667 [==============================] - 3s 191us/step - loss: 0.0171 - accuracy: 0.9980
Epoch 5/6
16667/16667 [==============================] - 3s 189us/step - loss: 0.0047 - accuracy: 0.9999
Epoch 6/6
8333/8333 [==============================] - 0s 30us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 187us/step - loss: 0.5424 - accuracy: 0.7066
Epoch 2/2
25000/25000 [==============================] - 5s 199us/step - loss: 0.2389 - accuracy: 0.9086
Wall time: 6min 54s


GridSearchCV(cv=3, error_score=nan,
             estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD051FB208>,
             iid='deprecated', n_jobs=None,
             param_grid={'batch_size': [64, 128], 'epochs': [2, 4, 6]},
             pre_dispatch='2*n_jobs', refit=True, return_train_score=False,
             scoring='roc_auc', verbose=0)

In [16]:
grid_search.best_params_

{'batch_size': 128, 'epochs': 2}

In [17]:
grid_search.best_score_

0.930216994468223

In [27]:
# create function to print results

import tabulate

def search_results(cvres):
    
    columns = []
    table = []
    
    for key in param_grid.keys():

        columns.append(key)
    
    columns.append(grid_search.scoring)

    for mean_score, params in sorted(zip(cvres['mean_test_score'], cvres['params']), reverse=True):
        
        row = []

        for key in param_grid.keys():
            
            row.append(params[key])
        
        row.append(mean_score)
        table.append(row)
            
    print(tabulate.tabulate(table, headers=columns, tablefmt='fancy_grid'))

In [28]:
search_results(grid_search.cv_results_)

╒══════════╤══════════════╤═══════════╕
│   epochs │   batch_size │   roc_auc │
╞══════════╪══════════════╪═══════════╡
│        2 │          128 │  0.930217 │
├──────────┼──────────────┼───────────┤
│        6 │          128 │  0.923687 │
├──────────┼──────────────┼───────────┤
│        4 │          128 │  0.923328 │
├──────────┼──────────────┼───────────┤
│        6 │           64 │  0.922947 │
├──────────┼──────────────┼───────────┤
│        2 │           64 │  0.921492 │
├──────────┼──────────────┼───────────┤
│        4 │           64 │  0.920784 │
╘══════════╧══════════════╧═══════════╛


From this grid search of only two hyperparameters, the best option for the **`batch size` seems to be 128**, while using **2 as the number of `epochs` seems to give a slight better result**.

As an alternative to this printing option with **Tabulate**, we could also have used **Pandas**.

In [29]:
df_cv_results = pd.DataFrame(grid_search.cv_results_['params'], columns = ['epochs', 'batch_size'])

In [30]:
df_cv_results['roc_auc'] = grid_search.cv_results_['mean_test_score']

In [31]:
df_cv_results.sort_values(by=['roc_auc'], ascending=False)

epochs  batch_size   roc_auc
3       2         128  0.930217
5       6         128  0.923687
4       4         128  0.923328
2       6          64  0.922947
0       2          64  0.921492
1       4          64  0.920784

To remove the index, we have several options. We'll illustrate some examples for the top 5 results.

In [33]:
# Method 1

print(df_cv_results.sort_values(by=['roc_auc'], ascending=False).head().to_string(index=False))

 epochs  batch_size   roc_auc
      2         128  0.930217
      6         128  0.923687
      4         128  0.923328
      6          64  0.922947
      2          64  0.921492


In [34]:
# Method 2

from IPython.display import display, HTML
display(HTML(df_cv_results.sort_values(by=['roc_auc'], ascending=False).head().to_html(index=False)))

In [35]:
# Method 3

df_cv_results.sort_values(by=['roc_auc'], ascending=False).head().style.hide_index()

We can now try to to tune some other hyperparameteres, like `n_dense` and `dropout`.

#### 8. Create model

In [53]:
model = KerasClassifier(build_fn=create_model, epochs=2, batch_size=128, verbose=1)

#### 9. Define grid search parameters: `n_dense` and `dropout`

In [54]:
n_dense = [64, 128]
dropout = [0.2, 0.5]

param_grid = {'n_dense': n_dense, 'dropout': dropout}

In [55]:
param_grid

{'n_dense': [64, 128], 'dropout': [0.2, 0.5]}

In [56]:
grid_search = GridSearchCV(model, param_grid, cv=3, scoring = 'roc_auc')

#### 10. Perform grid search and print results

In [57]:
%%time

grid_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16666/16666 [==============================] - 3s 199us/step - loss: 0.6000 - accuracy: 0.6538
Epoch 2/2
8334/8334 [==============================] - 0s 28us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16667/16667 [==============================] - 3s 208us/step - loss: 0.5773 - accuracy: 0.6800
Epoch 2/2
8333/8333 [==============================] - 0s 28us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16667/16667 [==============================] - 4s 253us/step - loss: 0.5835 - accuracy: 0.6734
Epoch 2/2
8333/8333 [==============================] - 0s 37us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 190us/step - loss: 0.5539 - accuracy: 0.6966
Epoch 2/2
25000/25000 [==============================] - 5s 183us/step - loss: 0.2552 - accuracy: 0.9024
Wall time: 1min 49s


GridSearchCV(cv=3, error_score=nan,
             estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD2E5C76C8>,
             iid='deprecated', n_jobs=None,
             param_grid={'dropout': [0.2, 0.5], 'n_dense': [64, 128]},
             pre_dispatch='2*n_jobs', refit=True, return_train_score=False,
             scoring='roc_auc', verbose=0)

In [58]:
grid_search.best_params_

{'dropout': 0.5, 'n_dense': 64}

In [59]:
grid_search.best_score_

0.9291520313337686

In [60]:
search_results(grid_search.cv_results_)

╒═══════════╤═══════════╤═══════════╕
│   n_dense │   dropout │   roc_auc │
╞═══════════╪═══════════╪═══════════╡
│        64 │       0.5 │  0.929152 │
├───────────┼───────────┼───────────┤
│        64 │       0.2 │  0.927046 │
├───────────┼───────────┼───────────┤
│       128 │       0.5 │  0.92592  │
├───────────┼───────────┼───────────┤
│       128 │       0.2 │  0.920134 │
╘═══════════╧═══════════╧═══════════╛


This time around, we obtain our best result with **64 neurons for `n_dense`** and a **`dropout` value of 0.5**.

Like we did before, we can also use Pandas to print this table.

In [63]:
df_cv_results = pd.DataFrame(grid_search.cv_results_['params'], columns = ['n_dense', 'dropout'])

df_cv_results['roc_auc'] = grid_search.cv_results_['mean_test_score']

df_cv_results.sort_values(by=['roc_auc'], ascending=False).style.hide_index()
# why the change in the number of decimal places in the dropout column?!

Interestingly enough, the format of the dropout column is changed. We can easily correct that.

In [64]:
format_dict = {'dropout': '{:.1f}'}
df_cv_results.sort_values(by=['roc_auc'], ascending=False).style.format(format_dict).hide_index()

Even though we are using a very simple model and have only tried to tune 2 hyperparameters at a time with 2 or 3 values for each, we can already see that this process can be somewhat time consuming.

Not only that, but it also makes sense to tune all the hyperparameters together because they are not independent from one another in the way they affect the model's performance. As a side effect, the time to perform this kind of grid search will increase tremendously.

Let's see what happens when we tune all the hyperparameters in one go.

#### 11. Create model

In [44]:
model = KerasClassifier(build_fn=create_model, verbose=1)

#### 12. Define grid search parameters: `epochs`, `batch_size`, `n_dense` and `dropout`

In [45]:
epochs = [2, 4, 6]
batch_size = [64, 128]

n_dense = [64, 128]
dropout = [0.2, 0.5]

param_grid = {'epochs': epochs, 'batch_size': batch_size, 
              'n_dense': n_dense, 'dropout': dropout}

In [46]:
param_grid

{'epochs': [2, 4, 6],
 'batch_size': [64, 128],
 'n_dense': [64, 128],
 'dropout': [0.2, 0.5]}

In [47]:
grid_search = GridSearchCV(model, param_grid, cv=3, scoring = 'roc_auc')

#### 13. Perform grid search and print results

In [48]:
%%time

grid_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16666/16666 [==============================] - 6s 358us/step - loss: 0.5222 - accuracy: 0.7215
Epoch 2/2
8334/8334 [==============================] - 0s 34us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
16667/16667 [==============================] - 5s 313us/step - loss: 0.5074 - accuracy: 0.7317
Epoch 2/2
8333/8333 [==============================] - 0s 36us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/6
16667/16667 [==============================] - 4s 254us/step - loss: 0.5754 - accuracy: 0.6782
Epoch 2/6
16667/16667 [==============================] - 4s 255us/step - loss: 0.2390 - accuracy: 0.9071
Epoch 3/6
16667/16667 [==============================] - 4s 245us/step - loss: 0.0524 - accuracy: 0.9888
Epoch 4/6
16667/16667 [==============================] - 4s 241us/step - loss: 0.0074 - accuracy: 0.9997
Epoch 5/6
16667/16667 [==============================] - 4s 246us/step - loss: 0.0024 - accuracy: 1.0000
Epoch 6/6
8333/8333 [==============================] - 0s 37us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 189us/step - loss: 0.5388 - accuracy: 0.7048
Epoch 2/2
25000/25000 [==============================] - 5s 181us/step - loss: 0.2422 - accuracy: 0.9074
Wall time: 26min 51s


GridSearchCV(cv=3, error_score=nan,
             estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD1CE68548>,
             iid='deprecated', n_jobs=None,
             param_grid={'batch_size': [64, 128], 'dropout': [0.2, 0.5],
                         'epochs': [2, 4, 6], 'n_dense': [64, 128]},
             pre_dispatch='2*n_jobs', refit=True, return_train_score=False,
             scoring='roc_auc', verbose=0)

In [49]:
grid_search.best_params_

{'batch_size': 128, 'dropout': 0.5, 'epochs': 2, 'n_dense': 64}

In [50]:
grid_search.best_score_

0.9295886151028102

In [51]:
search_results(grid_search.cv_results_)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.5 │  0.929589 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.2 │  0.927909 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │       128 │       0.5 │  0.925998 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.5 │  0.924446 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.2 │  0.92349  │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │       128 │       0.5 │  0.92344  │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │           64 │        64 │ 

Tuning all the hyperparameters at the same time, we get the best results for **2 `epochs`** with a **`batchsize`of 128**, **64 neurons as `n_dense`** and **0.5 as our `dropout`** value.

However, even for a relatively simple model and only two or three options for each of the four hyperparameters we've decided to tune (and with a low cross-validation value of 3), this grid search took more than 25 minutes to complete.

One alternative is to use all the cores of our CPU to speed up the process.

In [52]:
import multiprocessing

# number of cores
multiprocessing.cpu_count()

4

Since we have 4 cores, we could set our parameter `n_jobs=4`. Alternatively, we could set it to `n_jobs=-1`, and it will assume the number of available cores of the machine.

We just needed to define our new `grid_search` variable and start the grid search.

In [ ]:
grid_search = GridSearchCV(model, param_grid, n_jobs=-1, cv=3, scoring = 'roc_auc')

In [ ]:
%%time

grid_search.fit(x_train, y_train)

However this raises 2 problems:

* the full progress of the search does not output to the notebook itself but only to the terminal window
* using this parameter may also interfere with the main neural network training process

With this in mind, we've decided not to use this option.

Another alternative is to perform a **random search** instead. This will be our **step 2**.

### Step 2

#### 1. Perform necessary imports

In [75]:
from sklearn.model_selection import RandomizedSearchCV

#import scipy.stats as ss

#### 2. Define random search parameters

In [76]:
epochs = [2, 4, 6]
batch_size = [64, 128]

n_dense = [64, 128]
dropout = [0, 0.1, 0.2, 0.3, 0.4, 0.5]

param_grid = {'epochs': epochs, 'batch_size': batch_size, 
              'n_dense': n_dense, 'dropout': dropout}

In [77]:
param_grid

{'epochs': [2, 4, 6],
 'batch_size': [64, 128],
 'n_dense': [64, 128],
 'dropout': [0, 0.1, 0.2, 0.3, 0.4, 0.5]}

In [78]:
rand_search = RandomizedSearchCV(model, param_grid, cv=5, scoring = 'roc_auc')

We've increased the number of possibilities for our hyperparameters.

For more solid results, we will use a **cross-validation value of 5** and will use the default value for the number of iterations, `n_iter=10`. This means that from the 72 (3x2x2x6) possibilities we will randomly test only 10.

#### 3. Perform random search and print results

In [79]:
%%time

rand_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/4
20000/20000 [==============================] - 4s 187us/step - loss: 0.5652 - accuracy: 0.6872
Epoch 2/4
20000/20000 [==============================] - 4s 178us/step - loss: 0.2334 - accuracy: 0.9104
Epoch 3/4
20000/20000 [==============================] - 4s 185us/step - loss: 0.0522 - accuracy: 0.9883
Epoch 4/4
5000/5000 [==============================] - 0s 31us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/4
20000/20000 [==============================] - 4s 191us/step - loss: 0.5578 - accuracy: 0.6888
Epoch 2/4
20000/20000 [==============================] - 4s 198us/step - loss: 0.2244 - accuracy: 0.9136
Epoch 3/4
20000/20000 [==============================] - 4s 206us/step - loss: 0.0475 - accuracy: 0.9901
Epoch 4/4
5000/5000 [==============================] - 0s 31us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/6
20000/20000 [==============================] - 4s 182us/step - loss: 0.5502 - accuracy: 0.6945
Epoch 2/6
20000/20000 [==============================] - 4s 182us/step - loss: 0.2182 - accuracy: 0.9177
Epoch 3/6
20000/20000 [==============================] - 4s 180us/step - loss: 0.0419 - accuracy: 0.9923
Epoch 4/6
20000/20000 [==============================] - 4s 187us/step - loss: 0.0051 - accuracy: 0.9999
Epoch 5/6
20000/20000 [==============================] - 4s 183us/step - loss: 0.0016 - accuracy: 1.00001s
Epoch 6/6
5000/5000 [==============================] - 0s 34us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 181us/step - loss: 0.5043 - accuracy: 0.7360
Epoch 2/2
25000/25000 [==============================] - 5s 184us/step - loss: 0.2073 - accuracy: 0.9220
Wall time: 18min 30s


RandomizedSearchCV(cv=5, error_score=nan,
                   estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD2E5C76C8>,
                   iid='deprecated', n_iter=10, n_jobs=None,
                   param_distributions={'batch_size': [64, 128],
                                        'dropout': [0, 0.1, 0.2, 0.3, 0.4, 0.5],
                                        'epochs': [2, 4, 6],
                                        'n_dense': [64, 128]},
                   pre_dispatch='2*n_jobs', random_state=None, refit=True,
                   return_train_score=False, scoring='roc_auc', verbose=0)

In [80]:
rand_search.best_params_

{'n_dense': 64, 'epochs': 2, 'dropout': 0.1, 'batch_size': 128}

In [81]:
rand_search.best_score_

0.9270258352674942

In [82]:
search_results(rand_search.cv_results_)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.1 │  0.927026 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        4 │          128 │        64 │       0.3 │  0.925024 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.1 │  0.924337 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │           64 │        64 │       0.5 │  0.924077 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │       128 │       0.3 │  0.923023 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        4 │          128 │       128 │       0.5 │  0.922457 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │           64 │       128 │ 

From this first run, we can reasonably assume that the best values for **`batch_size`** and **`n_dense`** are, respectively, **128** and **64**.

We will now keep the same possible values for the number of `epochs` and try slightly different values for the `dropout` value.

#### 4. Define random search parameters

In [85]:
# obtain 10 values sampled from a uniform distribution between 0.1 and 0.6 ([loc, loc + scale])

#ss.uniform(loc=0.1, scale=0.5).rvs(10)

In [86]:
epochs = [2, 4, 6]
batch_size = [128]

n_dense = [64]
dropout = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6]
# dropout = ss.uniform(loc=0.1, scale=0.5)

param_grid = {'epochs': epochs, 'batch_size': batch_size, 
              'n_dense': n_dense, 'dropout': dropout}

In [87]:
rand_search = RandomizedSearchCV(model, param_grid, cv=5, scoring = 'roc_auc')

#### 5. Perform random search and print results

In [88]:
%%time

rand_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/4
20000/20000 [==============================] - 4s 208us/step - loss: 0.5832 - accuracy: 0.6678
Epoch 2/4
20000/20000 [==============================] - 4s 178us/step - loss: 0.2554 - accuracy: 0.8998
Epoch 3/4
20000/20000 [==============================] - 4s 187us/step - loss: 0.0743 - accuracy: 0.9805
Epoch 4/4
5000/5000 [==============================] - 0s 37us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/4
20000/20000 [==============================] - 4s 185us/step - loss: 0.5800 - accuracy: 0.6762
Epoch 2/4
20000/20000 [==============================] - 4s 191us/step - loss: 0.2603 - accuracy: 0.8973
Epoch 3/4
20000/20000 [==============================] - 4s 198us/step - loss: 0.0793 - accuracy: 0.9799
Epoch 4/4
5000/5000 [==============================] - 0s 31us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/4
20000/20000 [==============================] - 4s 192us/step - loss: 0.5484 - accuracy: 0.7053
Epoch 2/4
20000/20000 [==============================] - 4s 194us/step - loss: 0.2205 - accuracy: 0.9148
Epoch 3/4
20000/20000 [==============================] - 4s 187us/step - loss: 0.0452 - accuracy: 0.9911
Epoch 4/4
5000/5000 [==============================] - 0s 31us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 188us/step - loss: 0.5300 - accuracy: 0.7145
Epoch 2/2
25000/25000 [==============================] - 5s 195us/step - loss: 0.2381 - accuracy: 0.9091
Wall time: 13min 22s


RandomizedSearchCV(cv=5, error_score=nan,
                   estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD2E5C76C8>,
                   iid='deprecated', n_iter=10, n_jobs=None,
                   param_distributions={'batch_size': [128],
                                        'dropout': [0.1, 0.2, 0.3, 0.4, 0.5,
                                                    0.6],
                                        'epochs': [2, 4, 6], 'n_dense': [64]},
                   pre_dispatch='2*n_jobs', random_state=None, refit=True,
                   return_train_score=False, scoring='roc_auc', verbose=0)

In [89]:
rand_search.best_params_

{'n_dense': 64, 'epochs': 2, 'dropout': 0.5, 'batch_size': 128}

In [90]:
rand_search.best_score_

0.9318239050957734

In [91]:
search_results(rand_search.cv_results_)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.5 │  0.931824 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.4 │  0.929686 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.2 │  0.92927  │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.1 │  0.927133 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.6 │  0.925528 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.2 │  0.924949 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │ 

The value **2** for the number of **`epochs`** seems to be the best.

We can focus only on the `dropout` value.

#### 5. Define random search parameters

In [92]:
epochs = [2]
batch_size = [128]

n_dense = [64]
dropout = [0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8]

param_grid = {'epochs': epochs, 'batch_size': batch_size, 
              'n_dense': n_dense, 'dropout': dropout}

In [93]:
rand_search = RandomizedSearchCV(model, param_grid, cv=5, scoring = 'roc_auc')

#### 7. Perform random search and print results

In [94]:
%%time

rand_search.fit(x_train, y_train)

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\sklearn\model_selection\_search.py:281: UserWarning: The total space of parameters 7 is smaller than n_iter=10. Running 7 iterations. For exhaustive searches, use GridSearchCV.
  % (grid_size, self.n_iter, grid_size), UserWarning)
C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
20000/20000 [==============================] - 4s 204us/step - loss: 0.5304 - accuracy: 0.7127
Epoch 2/2
5000/5000 [==============================] - 0s 44us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
20000/20000 [==============================] - 4s 186us/step - loss: 0.5460 - accuracy: 0.7032
Epoch 2/2
5000/5000 [==============================] - 0s 31us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


...

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
20000/20000 [==============================] - 5s 227us/step - loss: 0.6609 - accuracy: 0.5911
Epoch 2/2
5000/5000 [==============================] - 0s 34us/step


C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/2
25000/25000 [==============================] - 5s 212us/step - loss: 0.6266 - accuracy: 0.6218
Epoch 2/2
25000/25000 [==============================] - 6s 229us/step - loss: 0.3228 - accuracy: 0.8708
Wall time: 5min 47s


RandomizedSearchCV(cv=5, error_score=nan,
                   estimator=<keras.wrappers.scikit_learn.KerasClassifier object at 0x000001BD2E5C76C8>,
                   iid='deprecated', n_iter=10, n_jobs=None,
                   param_distributions={'batch_size': [128],
                                        'dropout': [0.2, 0.3, 0.4, 0.5, 0.6,
                                                    0.7, 0.8],
                                        'epochs': [2], 'n_dense': [64]},
                   pre_dispatch='2*n_jobs', random_state=None, refit=True,
                   return_train_score=False, scoring='roc_auc', verbose=0)

In [95]:
rand_search.best_params_

{'n_dense': 64, 'epochs': 2, 'dropout': 0.8, 'batch_size': 128}

In [96]:
rand_search.best_score_

0.931809343846745

In [97]:
search_results(rand_search.cv_results_)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.8 │  0.931809 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.6 │  0.931699 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.7 │  0.931128 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.4 │  0.929987 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.5 │  0.929799 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.3 │  0.92869  │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │ 

Since we kept the number of iterations at 10 and we only have 7 possible combinations of values, we've explored all the possibilities. This time, the value 0.8 for `dropout` seems to allow us to achieve the best result. Anyway, all values from 0.4 to 0.8 seem to allow for a good performance of our model.

Even with a random search, this hyperparameter tuning task seems to be quite time consuming.

We can move to the **cloud** to see if we can complete the hyperparameter tuning in less time. With this improvement in computing resources, we can also try to tune **more complex models**. This is something we can explore on a different project.

Another alternative is to try a different method to tune our hyperparameters. One option is **Bayesian optimization (BO)**, that uses probabilistic models to select better configurations. We will try to implement this in our **step 3** with the help of **Hyperopt**.

### Step 3

#### 1. Perform necessary imports

In [10]:
from sklearn.model_selection import cross_val_score
import time

from hyperopt import fmin, tpe, hp, Trials, STATUS_OK

#### 2. Define objective function

In [11]:
def objective(params):

    model = KerasClassifier(build_fn=create_model, **params)
    
    start = time.time()

    cv_mean_score = cross_val_score(model, x_train, y_train, cv=5, scoring = 'roc_auc').mean()

    loss = -cv_mean_score
    
    end = (time.time() - start) / 60

    return {'loss': loss, 
            'status': STATUS_OK, 
            'params': params, 
            'eval_time': '{0:.2f}'.format(end)+' minutes'}

#### 3. Define search space

In [12]:
space = {'epochs': hp.choice('epochs', [2, 4, 6]), 
         'batch_size': hp.choice('batch_size', [64, 128]), 
         'n_dense': hp.choice('n_dense', [64, 128]), 
         'dropout': hp.choice('dropout', [0.2, 0.5])}

Hyperopt implements several algorithms. We'll be using an algorithm known as **tree of parzen estimators (tpe)** to perform our search.

#### 4. Perform BO and print results

In [13]:
%%time

trials = Trials()

best = fmin(fn = objective, 
            space = space, 
            algo = tpe.suggest, 
            max_evals = 10, 
            trials = trials)

  0%|                                                                    | 0/10 [00:00<?, ?trial/s, best loss=?]

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "



Epoch 1/4                                                                                                       
  128/20000 [..............................]                                                                    
 - ETA: 48s - loss: 0.6948 - accuracy: 0.4609                                                                   
                                                                                                                
  384/20000 [..............................]                                                                    
 - ETA: 19s - loss: 0.6943 - accuracy: 0.4844                                                                   
                                                                                                                
  640/20000 [..............................]                                                                    
 - ETA: 13s - loss: 0.6963 - accuracy: 0.4891                                                   

                                                                                                               
 4864/20000 [======>.......................]                                                                    
 - ETA: 6s - loss: 0.6930 - accuracy: 0.5076                                                                    
                                                                                                               
 5120/20000 [======>.......................]                                                                    
 - ETA: 6s - loss: 0.6924 - accuracy: 0.5094                                                                    
                                                                                                               
 5376/20000 [=======>......................]                                                                    
 - ETA: 5s - loss: 0.6920 - accuracy: 0.5108                                                       

                                                                                                               
10496/20000 [==============>...............]                                                                    
 - ETA: 3s - loss: 0.6774 - accuracy: 0.5724                                                                    
                                                                                                               
10752/20000 [===============>..............]                                                                    
 - ETA: 3s - loss: 0.6755 - accuracy: 0.5763                                                                    
                                                                                                               
11008/20000 [===============>..............]                                                                    
 - ETA: 3s - loss: 0.6736 - accuracy: 0.5800                                                       

...

                                                                                                               
 7424/20000 [==========>...................]                                                                    
 - ETA: 3s - loss: 0.6926 - accuracy: 0.5090                                                                    
                                                                                                               
 7680/20000 [==========>...................]                                                                    
 - ETA: 3s - loss: 0.6926 - accuracy: 0.5086                                                                    
                                                                                                               
 7936/20000 [==========>...................]                                                                    
 - ETA: 2s - loss: 0.6926 - accuracy: 0.5092                                                       

                                                                                                               
14464/20000 [====================>.........]                                                                    
 - ETA: 1s - loss: 0.6654 - accuracy: 0.5877                                                                    
                                                                                                               
14720/20000 [=====================>........]                                                                    
 - ETA: 1s - loss: 0.6626 - accuracy: 0.5912                                                                    
                                                                                                               
14976/20000 [=====================>........]                                                                    
 - ETA: 1s - loss: 0.6605 - accuracy: 0.5939                                                       

                                                                                                               
 1664/20000 [=>............................]                                                                    
 - ETA: 4s - loss: 0.3034 - accuracy: 0.8870                                                                    
                                                                                                               
 1920/20000 [=>............................]                                                                    
 - ETA: 4s - loss: 0.3008 - accuracy: 0.8880                                                                    
                                                                                                               
 2176/20000 [==>...........................]                                                                    
 - ETA: 4s - loss: 0.2977 - accuracy: 0.8915                                                       

                                                                                                               
 8576/20000 [===========>..................]                                                                    
 - ETA: 2s - loss: 0.2805 - accuracy: 0.8896                                                                    
                                                                                                               
 8832/20000 [============>.................]                                                                    
 - ETA: 2s - loss: 0.2806 - accuracy: 0.8897                                                                    
                                                                                                               
 9216/20000 [============>.................]                                                                    
 - ETA: 2s - loss: 0.2792 - accuracy: 0.8900                                                       

                                                                                                               
15616/20000 [======================>.......]                                                                    
 - ETA: 1s - loss: 0.2753 - accuracy: 0.8904                                                                    
                                                                                                               
16000/20000 [=======================>......]                                                                    
 - ETA: 0s - loss: 0.2763 - accuracy: 0.8899                                                                    
                                                                                                               
16256/20000 [=======================>......]                                                                    
 - ETA: 0s - loss: 0.2771 - accuracy: 0.8895                                                       

In [50]:
print(best)

{'batch_size': 1, 'dropout': 1, 'epochs': 0, 'n_dense': 0}


Printing our best result like this is not very informative because we get the indices of our lists of possible parameters instead of the values themselves. To get the values, we can do this:

In [51]:
from hyperopt import space_eval

print(space_eval(space, best))

{'batch_size': 128, 'dropout': 0.5, 'epochs': 2, 'n_dense': 64}


From the 24 (3x2x2x2) possible combinations, we've only performed 10 iterations (`max_evals = 10`). As before for a similar search, our best parameters are 128 for `batch_size`, 0.5 for `dropout`, 2 for `epochs` and 64 for `n_dense`.

As for our best value in terms of ROC AUC:

In [59]:
-min(trials.losses())

0.9311468433351319

Let's print a table with all the information.

In [60]:
# create function to print results

from operator import itemgetter

def bo_results(trials_res):
    
    columns = ['epochs', 'batch_size', 'n_dense', 'dropout', 'roc_auc']
    table = []

    for result in trials_res:
                    
        row = []

        for _, value in result['params'].items():

            row.append(value)
                
        ordered_row = [row[2], row[0], row[3], row[1]]

        ordered_row.append(-result['loss'])

        table.append(ordered_row)
    
    ordered_table = sorted(table, key=itemgetter(4), reverse=True)
                
    print(tabulate.tabulate(ordered_table, headers=columns, tablefmt='fancy_grid'))

In [61]:
bo_results(trials.results)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.5 │  0.931147 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.5 │  0.930699 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │       128 │       0.5 │  0.926784 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        6 │          128 │        64 │       0.5 │  0.925734 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        4 │          128 │        64 │       0.5 │  0.924614 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        4 │          128 │       128 │       0.5 │  0.922735 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        4 │           64 │        64 │ 

To finish things up, we can do a similar search to the one we did on point 5. of step 2, restricting the number of iterations to 5.

#### 5. Define search space

In [62]:
space = {'epochs': hp.choice('epochs', [2]), 
         'batch_size': hp.choice('batch_size', [128]), 
         'n_dense': hp.choice('n_dense', [64]), 
         'dropout': hp.choice('dropout', [0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8])}

#### 6. Perform BO and print results

In [63]:
%%time

trials = Trials()

best = fmin(fn = objective, 
            space = space, 
            algo = tpe.suggest, 
            max_evals = 5, 
            trials = trials)

  0%|                                                                     | 0/5 [00:00<?, ?trial/s, best loss=?]

C:\Users\joaon\Anaconda3\envs\DL-illustrated\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:433: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "



Epoch 1/2                                                                                                       
  128/20000 [..............................]                                                                    
 - ETA: 26s - loss: 0.6948 - accuracy: 0.5000                                                                   
                                                                                                                
  512/20000 [..............................]                                                                    
 - ETA: 9s - loss: 0.6937 - accuracy: 0.5078                                                                    
                                                                                                               
  768/20000 [>.............................]                                                                    
 - ETA: 7s - loss: 0.6945 - accuracy: 0.5065                                                     

                                                                                                               
 5888/20000 [=======>......................]                                                                    
 - ETA: 4s - loss: 0.6896 - accuracy: 0.5289                                                                    
                                                                                                               
 6016/20000 [========>.....................]                                                                    
 - ETA: 4s - loss: 0.6893 - accuracy: 0.5294                                                                    
                                                                                                               
 6272/20000 [========>.....................]                                                                    
 - ETA: 4s - loss: 0.6885 - accuracy: 0.5322                                                       

                                                                                                               
11136/20000 [===============>..............]                                                                    
 - ETA: 2s - loss: 0.6470 - accuracy: 0.6104                                                                    
                                                                                                               
11392/20000 [================>.............]                                                                    
 - ETA: 2s - loss: 0.6432 - accuracy: 0.6146                                                                    
                                                                                                               
11648/20000 [================>.............]                                                                    
 - ETA: 2s - loss: 0.6386 - accuracy: 0.6191                                                       

...

                                                                                                               
12800/20000 [==================>...........]                                                                    
 - ETA: 1s - loss: 0.6759 - accuracy: 0.5832                                                                    
                                                                                                               
13056/20000 [==================>...........]                                                                    
 - ETA: 1s - loss: 0.6740 - accuracy: 0.5868                                                                    
                                                                                                               
13312/20000 [==================>...........]                                                                    
 - ETA: 1s - loss: 0.6721 - accuracy: 0.5897                                                       

                                                                                                               
18560/20000 [==========================>...]                                                                    
 - ETA: 0s - loss: 0.6077 - accuracy: 0.6517                                                                    
                                                                                                               
18816/20000 [===========================>..]                                                                    
 - ETA: 0s - loss: 0.6044 - accuracy: 0.6545                                                                    
                                                                                                               
19072/20000 [===========================>..]                                                                    
 - ETA: 0s - loss: 0.6021 - accuracy: 0.6565                                                       

                                                                                                               
 3584/20000 [====>.........................]                                                                    
 - ETA: 5s - loss: 0.2929 - accuracy: 0.8856                                                                    
                                                                                                               
 3712/20000 [====>.........................]                                                                    
 - ETA: 5s - loss: 0.2905 - accuracy: 0.8869                                                                    
                                                                                                               
 3968/20000 [====>.........................]                                                                    
 - ETA: 5s - loss: 0.2879 - accuracy: 0.8871                                                       

                                                                                                               
 9472/20000 [=============>................]                                                                    
 - ETA: 3s - loss: 0.2718 - accuracy: 0.8910                                                                    
                                                                                                               
 9728/20000 [=============>................]                                                                    
 - ETA: 3s - loss: 0.2726 - accuracy: 0.8907                                                                    
                                                                                                               
 9984/20000 [=============>................]                                                                    
 - ETA: 2s - loss: 0.2721 - accuracy: 0.8911                                                       

                                                                                                               
15360/20000 [======================>.......]                                                                    
 - ETA: 1s - loss: 0.2601 - accuracy: 0.8980                                                                    
                                                                                                               
15616/20000 [======================>.......]                                                                    
 - ETA: 1s - loss: 0.2590 - accuracy: 0.8984                                                                    
                                                                                                               
16000/20000 [=======================>......]                                                                    
 - ETA: 1s - loss: 0.2588 - accuracy: 0.8987                                                       

In [64]:
print(space_eval(space, best))

{'batch_size': 128, 'dropout': 0.8, 'epochs': 2, 'n_dense': 64}


In [65]:
-min(trials.losses())

0.9329192409662902

In [66]:
bo_results(trials.results)

╒══════════╤══════════════╤═══════════╤═══════════╤═══════════╕
│   epochs │   batch_size │   n_dense │   dropout │   roc_auc │
╞══════════╪══════════════╪═══════════╪═══════════╪═══════════╡
│        2 │          128 │        64 │       0.8 │  0.932919 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.7 │  0.931567 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.5 │  0.931029 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.3 │  0.927721 │
├──────────┼──────────────┼───────────┼───────────┼───────────┤
│        2 │          128 │        64 │       0.3 │  0.927268 │
╘══════════╧══════════════╧═══════════╧═══════════╧═══════════╛


Our search found the best result with only 5 iterations, so our BO algorithm seems to be doing a good job!

Oddly enough, the same set of values was used twice. Let's investigate this further.

In [68]:
trials.results

[{'loss': -0.9277208331320604,
  'status': 'ok',
  'params': {'batch_size': 128, 'dropout': 0.3, 'epochs': 2, 'n_dense': 64},
  'eval_time': '0.93 minutes'},
 {'loss': -0.9272682128887949,
  'status': 'ok',
  'params': {'batch_size': 128, 'dropout': 0.3, 'epochs': 2, 'n_dense': 64},
  'eval_time': '0.94 minutes'},
 {'loss': -0.9315672143946413,
  'status': 'ok',
  'params': {'batch_size': 128, 'dropout': 0.7, 'epochs': 2, 'n_dense': 64},
  'eval_time': '0.92 minutes'},
 {'loss': -0.9329192409662902,
  'status': 'ok',
  'params': {'batch_size': 128, 'dropout': 0.8, 'epochs': 2, 'n_dense': 64},
  'eval_time': '0.94 minutes'},
 {'loss': -0.9310290359957729,
  'status': 'ok',
  'params': {'batch_size': 128, 'dropout': 0.5, 'epochs': 2, 'n_dense': 64},
  'eval_time': '0.97 minutes'}]

Apparently, in the beginning of the evaluation the same set of values was used twice. This may have happened because our search space is relatively small, but it is still an odd behavior (see https://github.com/hyperopt/hyperopt/issues/370).

#### Conclusion

With this project, we've demonstrated the use of **3 different methods to perform hyperparameter tuning**.

With **Grid Search** we perform an exhaustive search of all the possible combinations of values - this can be very time consuming. 

One alternative is to use **Random Search**, which randomly selects some of the possible combinations. This means that we can perform our search in less time, but we can also miss the best combination of values. When we are dealing with continuous values (sampling from a distribution) and not discrete values, this option can also give us an advantage when compared to the set of discrete values we choose when performing a grid search.

A better alternative is to use **Bayesian Optimization**, that uses probabilistic models to select better configurations. In this way, only the most promising hyperparameters are selected, and the probabilistic model is iteratively updated based on past choices of hyperparameters.

There are **other alternatives to perform hyperparameter tuning**. 

Instead of performing a pure random search, we can perform a **random search with the Hyperband algorithm**, that uses early stopping. This means that models with a poor initial cross-validation accuracy are stopped before the cross-validation analysis completes, and only the best ones are run until the end.

Other alternative is to use **evolution-based algorithms**, like the [TPOT](https://github.com/EpistasisLab/tpot) library does.

Several other libraries implement these and other methods. Some interesting libraries to explore are:

* [Spearmint](https://github.com/JasperSnoek/spearmint)
* [SMAC](https://github.com/automl/SMAC3)
* [HpBandSter](https://github.com/automl/HpBandSter)
* [Keras Tuner](https://github.com/keras-team/keras-tuner)
* ...